## Libraries

In [1]:
#install.packages('mvtnorm')
#install.packages('MCMCpack')
#install.packages('tmvtnorm')
install.packages('diversitree')

Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)

also installing the dependency ‘subplex’




In [2]:
library(diversitree)
library(mvtnorm)
library(LaplacesDemon)
# library(tmvtnorm)
library(GA)
library(MASS)
library(Matrix)
library(matrixcalc)

Loading required package: ape


Attaching package: ‘LaplacesDemon’


The following objects are masked from ‘package:mvtnorm’:

    dmvt, rmvt


Loading required package: foreach

Loading required package: iterators

Package 'GA' version 3.2.4
Type 'citation("GA")' for citing this R package in publications.


Attaching package: ‘GA’


The following object is masked from ‘package:utils’:

    de



Attaching package: ‘matrixcalc’


The following objects are masked from ‘package:LaplacesDemon’:

    is.positive.definite, is.square.matrix, is.symmetric.matrix,
    lower.triangle, upper.triangle




## Download stock returns

## Function to select time period for stock returns 

In [3]:
stock_return_data = function(stock_vector,start_date,end_date,time_period,percentage = FALSE){
    if(!require(quantmod)) {
        install.packages("quantmod")
    }
    library("quantmod")
    stock_returns <- c()
    for (stock in stock_vector) {
    # Get stock data from Yahoo Finance
        getSymbols(stock, src = "yahoo", from = start_date, to = end_date, auto.assign = TRUE)
 
        # Adjusted closing prices
        stock_prices <- Ad(get(stock))
 
        # Calculate returns
        if(time_period == "daily"){
            stock_ret <- dailyReturn(stock_prices)
        }
        if(time_period == "weekly"){
            stock_ret <- weeklyReturn(stock_prices)
        }
        if(time_period == "monthly"){
            stock_ret <- monthlyReturn(stock_prices)
        }
        if(time_period == "quarterly"){
            stock_ret <- quarterlyReturn(stock_prices)
        }
        if(time_period == "yearly"){
            stock_ret <- yearlyReturn(stock_prices)
        }
 
        # Store returns in the list
        stock_returns[[stock]] <- stock_ret
    }
    merged_returns <- do.call(merge, stock_returns)
    colnames(merged_returns)=stock_vector
    merged_returns = as.data.frame(merged_returns)
    if(percentage == TRUE){
        merged_returns = merged_returns*100
    }
    return(merged_returns)
}

In [4]:
stocks <- c("BRK-B", "LLY", "MSFT", "AAPL","JPM","PG","WMT","NOV")
data = stock_return_data(stocks,"2019-01-01",Sys.Date(),"daily",percentage = TRUE)

Loading required package: quantmod

Loading required package: xts

Loading required package: zoo


Attaching package: ‘zoo’


The following objects are masked from ‘package:base’:

    as.Date, as.Date.numeric


Loading required package: TTR

Registered S3 method overwritten by 'quantmod':
  method            from
  as.zoo.data.frame zoo 



In [5]:
dim(data)

[1] 1442    8

In [6]:
write.csv(data,'stocks_data.csv')

In [7]:
R=data

In [8]:
tail(data)

BRK-B       LLY        MSFT       AAPL       JPM         PG        
2024-09-17  1.08459735 -1.8797221  0.8832934  0.2172642  0.66871903 -0.7673215
2024-09-18 -0.01751480 -0.1335300 -0.9973564  1.7989802 -0.82198386 -1.1144000
2024-09-19  0.68111811  1.1127449  1.8291137  3.7065533  1.42147977 -1.3684481
2024-09-20 -0.95712383  0.7048886 -0.7795968 -0.2927418  0.28981405  1.5623225
2024-09-23 -0.07247514 -0.3223009 -0.4043420 -0.7581051  0.16580895 -0.2582924
2024-09-24 -0.09231470  0.6434234 -1.0011294  0.3974009  0.07093922 -0.3050002
           WMT        NOV       
2024-09-17 -2.4329682  1.9912863
2024-09-18  0.5470742  0.2440568
2024-09-19 -1.2526862  2.8606166
2024-09-20  1.3070177  0.0000000
2024-09-23  1.6063804 -0.8875717
2024-09-24  0.4232495  0.0000000

## Likelihood Function

In [9]:
make.mvn <- function(mean, vcv) {
    logdet <- as.numeric(determinant(vcv, TRUE)$modulus)
    tmp <- length(mean) * log(2 * pi) + logdet
    vcv.i <- solve(vcv)

    function(x) {
        dx <- x - mean
        -(tmp + rowSums((dx %*% vcv.i) * dx))/2
    }
}
#N=5
#A=diag(5,5)
#a=rnorm(5)
#vcv = solve(A)
#mean=c(solve(A)%*%a)
#lik <- make.mvn(mean, vcv)
#set.seed(1)
#samples <- mcmc(lik, rep(0,5), 1000, 1, print.every = 100,lower=rep(0,5),upper=rep(Inf,5))

In [10]:
#samples

In [11]:
mat_symm = function(mat){
	mat[lower.tri(mat)] = 0
	mat_result = mat + t(mat) - diag(diag(mat),ncol = ncol(mat))
	return(mat_result)
}
# Example usage:
mat <- matrix(c(1, 2, 3, 4, 5, 6, 7, 8, 9), nrow = 3, ncol = 3) 
print("Original Matrix:")
print(mat)
 
updated_mat <- mat_symm(mat)
print("Matrix after replacing lower diagonal with upper diagonal:")
print(updated_mat)

[1] "Original Matrix:"
     [,1] [,2] [,3]
[1,]    1    4    7
[2,]    2    5    8
[3,]    3    6    9
[1] "Matrix after replacing lower diagonal with upper diagonal:"
     [,1] [,2] [,3]
[1,]    1    4    7
[2,]    4    5    8
[3,]    7    8    9


## Gibbs Sampler

In [28]:
# MCMC sampling function
mcmc_sampling <- function(R, n_iter) 
{
  N <- ncol(R)
  T <- nrow(R)
  
  # Initialize parameters
 mu <- rmvnorm(1,rep(0,N),diag(100, N))
 delta <- rmvnorm(N,rep(0,N),diag(100, N))
 sigma <- rinvwishart(S=diag(N,N),nu=N)
 Z <- t(rmvnorm(T, rep(0,N),diag(N))) 
 eta=c(mu,delta)  
  # Storage for MCMC samples
  mu_samples <- matrix(0, nrow = n_iter, ncol = N)
  Delta_samples <- array(0, dim = c(n_iter, N, N))
  Sigma_samples <- array(0, dim = c(n_iter, N, N))
  Z_samples <- array(0, dim = c(n_iter, T, N))
  
  for (iter in 1:n_iter) 
  {
    # Sample Z
    # Store MCMC samples
      s=array(0,dim=c(T,N,(N**2+N)))
      E_quant=array(0,dim=c(T,(N**2+N),(N**2+N)))
      e_quant=array(0,dim=c(T,(N**2+N),1))
      xi_quant=array(0,dim=c(T,N,N))
      a_quant=array(0,dim=c(T,N,1))
    for (t in 1:T)  
     {
    
        s[t,,]= cbind(diag(N),t(Z[,t])%x% diag(N))
        E_quant[t,,]=t(s[t,,])%*%solve(sigma,tol=1e-28)%*%s[t,,]
        e_quant[t,,]=t(s[t,,])%*%solve(sigma,tol=1e-28)%*% t(R[t,])
        print(paste('R= ',t(R[t,])))
        print(paste('mu=', t(mu)))
        mu=matrix(mu,nrow=N,ncol=1)
        xi_quant[t,,]=((t(R[t,])-mu)-((delta)%*%(Z[,t])))%*%t(((t(R[t,])-mu)-((delta)%*%(Z[,t]))))
        a_quant[t,,]= t(delta)%*%solve(sigma,tol=1e-28)%*%(t(R[t,])-mu)
    }
      
    E= apply(E_quant,c(2,3),sum) + diag((N+N**2))/100
    sym_E=mat_symm(solve(E,tol=1e-28))
    if(is.positive.semi.definite(sym_E)==F)
    sym_E=as.matrix(nearPD(sym_E)$mat) 
    e=apply(e_quant,c(2,3),sum)
    xi=apply(xi_quant,c(2,3),sum)+ diag(N,N)
    eta=rmvnorm(1,sym_E%*%e,sym_E)
    sigma= rinvwishart(S=xi,nu=(N+T))
    mu=eta[1:N]
    vec_delta=eta[(N+1):(N**2+N)]
    dim(vec_delta)=c(N,N)
    delta=vec_delta
    a=apply(a_quant,c(2,3),sum)
    A= diag(N)+(t(delta)%*%solve(sigma,tol=1e-28)%*%delta)
    vcv = solve(A)
    mean=c(solve(A)%*%a)
    lik <- make.mvn(mean, vcv)
    Z <- t(mcmc(lik, rep(0,N), T, 1,print.every=0,lower=rep(0,N),upper=rep(Inf,N))[,2:(N+1)])
    #print(Z)
    #Z= t(rtmvnorm(n=T,(solve(A)%*%a),solve(A),rep(0,N),rep(Inf,N)))
    #mu_samples[iter, ] <- mu
    #Delta_samples[iter, , ] <- delta
    #Sigma_samples[iter, , ] <- sigma
    #Z_samples[iter, , ] <- Z
    paste("current iteration= ", iter)
    skew_param_iter=list(mu_samples = mu,
              delta_samples = delta,
              sigma_samples = sigma,
              Z_samples = Z
              )
    save(skew_param_iter,file='skew_param_iter.RData')
      
  }
  
  # Discard burn-in samples
  #mu_samples <- mu_samples[(burn_in + 1):n_iter, ]
  #delta_samples <- Delta_samples[(burn_in + 1):n_iter, , ]
  #sigma_samples <- Sigma_samples[(burn_in + 1):n_iter, , ]
  #Z_samples <- Z_samples[(burn_in + 1):n_iter, , ]
  
  
  return(list(mu_samples = mu,
              delta_samples = delta,
              sigma_samples = sigma,
              Z_samples = Z
              ))
}

In [43]:
niter=15
vec_data=mcmc_sampling(data,niter)

[1] "R=  0" "R=  0" "R=  0" "R=  0" "R=  0" "R=  0" "R=  0" "R=  0"
[1] "mu= -12.6001998326545" "mu= -2.65622369815033" "mu= -3.52917921400597"
[4] "mu= -5.32967666553269" "mu= -6.97242421784537" "mu= -10.7305958428182"
[7] "mu= -6.56758732812857" "mu= -5.7695914182426" 
[1] "R=  -5.49309626331974"  "R=  -3.10756765186967"  "R=  -3.67883432799001" 
[4] "R=  -9.96071425936875"  "R=  -1.42116333392958"  "R=  -0.70113021134619" 
[7] "R=  -0.514240684604894" "R=  -0.618706078501163"
[1] "mu= -12.6001998326545" "mu= -2.65622369815033" "mu= -3.52917921400597"
[4] "mu= -5.32967666553269" "mu= -6.97242421784537" "mu= -10.7305958428182"
[7] "mu= -6.56758732812857" "mu= -5.7695914182426" 
[1] "R=  1.84701722763907"  "R=  3.00960964678125"  "R=  4.65094618485513" 
[4] "R=  4.26891549270958"  "R=  3.68652493593598"  "R=  2.04101636071878" 
[7] "R=  0.624600403950359" "R=  4.00777246986677" 
[1] "mu= -12.6001998326545" "mu= -2.65622369815033" "mu= -3.52917921400597"
[4] "mu= -5.32967666553269" "mu=

In [44]:
mu=vec_data[['mu_samples']];mu
delta=vec_data[['delta_samples']];delta
sigma=vec_data[['sigma_samples']];sigma

[1] -2.681464 -7.273734 -3.468636 14.451280 -2.651664  7.189679 -6.027857
[8] -4.367412

[,1]       [,2]        [,3]       [,4]       [,5]       [,6]      
[1,]  4.9099573   1.9020663  -8.219763 -6.1160942  5.0090360  -4.578541
[2,]  0.2435583   3.4725091  51.059554  0.7175712 11.4332466  -5.984422
[3,]  0.7011487  -0.4116213   4.293505  9.1357637 15.3547400 -12.879119
[4,] -1.7004934  -6.2312360  25.811381 -6.2494150 -6.1535173   5.209424
[5,] -2.4732038  11.4929608 -32.607101  5.2478639  0.9432684  11.690863
[6,] -0.5370664  -3.7221228  18.138427 -4.5740005  5.6751127  -2.543299
[7,] -2.2280093   7.9987865  13.128540  2.2677883 17.1166960  -1.566567
[8,] -4.4811534 -16.9748084   8.059187  1.8584087 -6.0356403  -1.905581
     [,7]       [,8]      
[1,] -20.667596   7.891662
[2,]  38.773261 -11.014118
[3,]  -5.280630   4.998220
[4,]  12.762446  -8.372709
[5,]  -4.055753  -5.725953
[6,]   9.311305   2.889732
[7,]   5.645024   4.396508
[8,]  -2.184614   1.694119

[,1]        [,2]       [,3]         [,4]        [,5]         [,6]        
[1,]  3573648453 -336416367  -5781692104  3880715271   7788392951  -6047944304
[2,]  -336416367   31830678    544819140  -366033399   -732674097    570154666
[3,] -5781692104  544819140   9355891875 -6281031426 -12598727109   9787527847
[4,]  3880715271 -366033399  -6281031426  4217754535   8454926631  -6571248860
[5,]  7788392951 -732674097 -12598727109  8454926631  16976022209 -13178241078
[6,] -6047944304  570154666   9787527847 -6571248860 -13178241078  10239484122
[7,] -8249233686  776971425  13347627127 -8960109383 -17976797768  13962845237
[8,] -3442680523  323895881   5569109287 -3737503852  -7503708264   5825316327
     [,7]         [,8]       
[1,]  -8249233686 -3442680523
[2,]    776971425   323895881
[3,]  13347627127  5569109287
[4,]  -8960109383 -3737503852
[5,] -17976797768 -7503708264
[6,]  13962845237  5825316327
[7,]  19043305183  7946345241
[8,]   7946345241  3316786602

In [45]:
skew_param=vec_data
save(skew_param,file='skew_param.RData')

In [46]:
#skew_param

## Predictive Moments

In [47]:
exp_z_mat = function(N){
    exp_val = function(z_ind1,z_ind2,z_ind3){
        if((z_ind1 == z_ind2) & (z_ind1 == z_ind3)){
            val = sqrt(8/pi)
        } else if((z_ind1 == z_ind2) | (z_ind1 == z_ind3) | (z_ind2 == z_ind3)){
            val = sqrt(2/pi)
        }else{
            val = (sqrt(2/pi))^3
        }
        return(val)
    }
    mat = matrix(nrow = N,ncol = N^2)
    for(i in 1:N){
        row_vec = c()
        ind = 1
        for(j in 1:N){
            for(k in 1:N){
                row_vec[ind] = exp_val(i,j,k)
                ind = ind + 1
            }
        }
        mat[i,] = row_vec
    }
    return(mat)
}
 
exp_z_mat(2)

[,1]      [,2]      [,3]      [,4]     
[1,] 1.5957691 0.7978846 0.7978846 0.7978846
[2,] 0.7978846 0.7978846 0.7978846 1.5957691

In [48]:
predictive_moments= function(mu,delta,sigma)
{
N=nrow(delta)
ones=rep(1,N)
m_hat=mu + (sqrt(2/pi))*delta%*%ones
V_hat= sigma + (1-(2/pi))*delta%*%t(delta)
EZ=exp_z_mat(N)
S_hat=(delta%*%EZ%*%(t(delta)%x%t(delta))) + 
3*t(mu)%x%((delta%*%t(delta))*(1-(2/pi))+ 
(2/pi)*delta%*%ones%*%t(delta%*%ones))+
3*(sqrt(2/pi)*t(delta%*%ones)%x%(sigma + mu%*%t(mu)))+
3*t(mu)%x% sigma+
mu%*%t(mu)%x% t(mu)-
3*t(m_hat)%x%V_hat-
m_hat%*%t(m_hat)%x%t(m_hat)
return(list(m=m_hat,V=V_hat,S=S_hat))
}

In [49]:
pred_moments=predictive_moments(mu,delta,sigma)

In [50]:
save(pred_moments,file='pred_moments.RData')

In [51]:
m=pred_moments[['m']];m
V=pred_moments[['V']];V
S=pred_moments[['S']];S

[,1]     
[1,] -18.53485
[2,]  63.49955
[3,]   9.22731
[4,]  26.48009
[5,] -15.00855
[6,]  26.84803
[7,]  31.28024
[8,] -20.30123

[,1]        [,2]       [,3]         [,4]        [,5]         [,6]        
[1,]  3573648695 -336416810  -5781692032  3880715061   7788393037  -6047944399
[2,]  -336416810   31832281    544819219  -366032753   -732674742    570155146
[3,] -5781692032  544819219   9355892077 -6281031504 -12598727197   9787527891
[4,]  3880715061 -366032753  -6281031504  4217754915   8454926307  -6571248654
[5,]  7788393037 -732674742 -12598727197  8454926307  16976022724 -13178241345
[6,] -6047944399  570155146   9787527891 -6571248654 -13178241345  10239484303
[7,] -8249233725  776971816  13347627253 -8960109310 -17976797902  13962845370
[8,] -3442680558  323895950   5569109290 -3737503744  -7503708433   5825316385
     [,7]         [,8]       
[1,]  -8249233725 -3442680558
[2,]    776971816   323895950
[3,]  13347627253  5569109290
[4,]  -8960109310 -3737503744
[5,] -17976797902 -7503708433
[6,]  13962845370  5825316385
[7,]  19043305399  7946345197
[8,]   7946345197  3316786756

[,1]      [,2]       [,3]       [,4]       [,5]      [,6]      
[1,] -1954.682  18433.390  5126.5548 -1625.4342 -2364.759  3615.8497
[2,] 18433.390 -70672.543 -9423.9626 11879.4209 -2760.483 -2521.7550
[3,]  5126.555  -9423.963  5213.4763  -828.1449 -1655.862  1714.3618
[4,] -1625.434  11879.421  -828.1449  4201.7423 -6746.631  2102.3000
[5,] -2364.759  -2760.483 -1655.8619 -6746.6310 12336.193 -5076.6061
[6,]  3615.850  -2521.755  1714.3618  2102.3000 -5076.606  2583.9015
[7,] 11899.356 -37441.392  -545.3983  1902.5919  1823.216  -400.2189
[8,] -4191.425   7790.657 -1135.2823  3967.8118 -5596.154  1451.8915
     [,7]        [,8]      [,9]        [,10]      [,11] [,12]      [,13]      
[1,]  11899.3562 -4191.425 -24091.6994  18647.669 ⋯       6428.084  -2075.2140
[2,] -37441.3921  7790.657  18647.6688  41726.276 ⋯      -3126.922   8166.0477
[3,]   -545.3983 -1135.282 -13503.8984  27890.677 ⋯       1442.901    596.6402
[4,]   1902.5919  3967.812  23598.2692 -94589.687 ⋯     -26093.776  -2374.4871
[5,]   1823.2157 -5596.154    868.6888  27644.540 ⋯       8806.735   9686.5766
[6,]   -400.2189  1451.891   6183.7264 -39718.959 ⋯     -16416.873    799.4520
[7,] -13086.3082 -1238.047  -8128.9494  54201.035 ⋯       1755.245   9098.3813
[8,]  -1238.0469  6640.677   1209.9207   6374.899 ⋯       9098.381 -15271.7941
     [,14]      [,15]      [,16]      [,17]      [,18]      [,19]     
[1,]   8007.140 -10506.529   3428.073 -11373.673   5773.247  -4817.418
[2,] -10506.529  -1715.505 -11714.306  46199.522 -31317.588  19059.328
[3,]   3428.073 -11714.306   2620.670   2367.788  -3902.805   1299.101
[4,] -11373.673  46199.522   2367.788  14745.493 -16633.127  12249.097
[5,]   5773.247 -31317.588  -3902.805 -16633.127  21681.662 -13564.454
[6,]  -4817.418  19059.328   1299.101  12249.097 -13564.454   9195.253
[7,]   2448.485 -26003.404  -5631.587  14984.188  -8128.845   3904.830
[8,]  -3260.976  18001.426   3434.748   1432.024  -4475.851   3688.226
     [,20]      [,21]    
[1,]   2448.485 -3260.976
[2,] -26003.404 18001.426
[3,]  -5631.587  3434.748
[4,]  14984.188  1432.024
[5,]  -8128.845 -4475.851
[6,]   3904.830  3688.226
[7,] -19190.612  8871.385
[8,]   8871.385 -1021.103

## Utility Function

In [52]:
expected_utility=function(w,m,V,S,lambda,gamma)
{
EU=(t(w)%*%m)-((lambda*t(w))%*%V%*%w)+(gamma*t(w)%*%S%*%(w%x%w))
return (EU)
}

## Genetic Algorithm to find optimal weights

In [53]:
N=dim(data)[2]
lower=rep(0,N)
upper=rep(1,N)
lambda=c(0,0.5,0.5,0.7,0.2)
gamma=c(0.5,0,0.5,0.2,0.7)
parameters=c("lambda","gamma")
result="expected_utility"
column_names=c(parameters,result,stocks)
result_df=data.frame(matrix(0,nrow=length(lambda),ncol=(3+N)))
colnames(result_df)=column_names
result_df$lambda=lambda
result_df$gamma=gamma
for (i in 1:dim(result_df)[1])
 {
ga_result = ga(
  type = "real-valued",
  fitness = function(w) expected_utility(w,m,V,S,result_df[i,1],result_df[i,2]) ,
  lower = lower,
  upper = upper,
  popSize = 150, # Population size
  maxiter = 700, # Maximum number of iterations
  run = 150 # Stop if the best solution doesn't improve after 100 iterations
)
   
    result_df[i,4:(dim(result_df)[2])]=ga_result@solution/sum(ga_result@solution)
    result_df[i,3]=ga_result@fitnessValue
    
    
    
    }

In [54]:
result_df

lambda gamma expected_utility BRK-B       LLY        MSFT       AAPL     
1 0.0    0.5   205653.762       0.004272779 0.16793684 0.16229051 0.1686380
2 0.5    0.0   -16088.708       0.120975162 0.03312908 0.08312107 0.2401865
3 0.5    0.5   -11139.995       0.139375131 0.01701713 0.08763577 0.2425278
4 0.7    0.2   -19648.485       0.129965550 0.04931931 0.11110129 0.2419017
5 0.2    0.7    -8870.591       0.117337737 0.07194611 0.10328203 0.2353102
  JPM        PG         WMT        NOV      
1 0.00149948 0.16559244 0.16394564 0.1658243
2 0.14499655 0.06352471 0.11153422 0.2025327
3 0.14260296 0.05659789 0.12757143 0.1866719
4 0.13185331 0.05308170 0.09919442 0.1835827
5 0.13744740 0.05712778 0.09978640 0.1777623

In [55]:
write.csv(result_df,'result_df.csv')

In [42]:
#install.packages('gganimate')